In [1]:
!pip install bitstring

In [2]:
!pip install nltk

In [3]:
import nltk
nltk.download('punkt')
nltk.download('stopwords')
nltk.download('wordnet')

[nltk_data] Downloading package punkt to
[nltk_data]     C:\Users\Nik\AppData\Roaming\nltk_data...
[nltk_data]   Package punkt is already up-to-date!
[nltk_data] Downloading package stopwords to
[nltk_data]     C:\Users\Nik\AppData\Roaming\nltk_data...
[nltk_data]   Package stopwords is already up-to-date!
[nltk_data] Downloading package wordnet to
[nltk_data]     C:\Users\Nik\AppData\Roaming\nltk_data...
[nltk_data]   Package wordnet is already up-to-date!


True

In [4]:
from nltk.tokenize import word_tokenize
from nltk.corpus import stopwords

In [8]:
from __future__ import annotations
import logging
import re
from collections import defaultdict
import math
import os
import string
import sys
import struct
import logging
import bitstring
from bitstring import Bits, BitArray, BitStream, pack

In [11]:
# Получаем текущую рабочую директорию
current_dir = os.getcwd()

In [9]:
DEFAULT_INVERTED_INDEX_STORE_PATH = os.path.join(current_dir, 'inverted_index.bin')
DATASET_BIG_PATH = os.path.join(current_dir, 'wikipedia_sample_tiny.txt')

In [15]:
DEFAULT_INVERTED_INDEX_STORE_PATH = os.path.join(current_dir, 'anna_inverted_index.bin')
DATASET_BIG_PATH = os.path.join(current_dir, 'anna.txt')

In [17]:
logger = logging.getLogger("InvertedIndex")

In [19]:
class InvertedIndex:
    """Inverted index implementation"""
    def __init__(self, documents: list):
        """Constructor for class InvertedIndex"""
        # обычный список  key -> list[int]
        self.inverted_index = defaultdict(list)
        # закодированный список key -> list[byte]
        self.posting_list_encoded = defaultdict(list)
        # обычный список skip list
        self.inverted_index_skip_list = defaultdict(list)
        # закодированный список skip list
        self.skip_list_encoded = defaultdict(list)
        self.use_skip_list = True
        # сохраняем количество документов (нужно для операции NOT)
        self.num_docs = len(documents)
        logger.info("Start tokenization documents list...")
        for doc_id, doc in enumerate(documents):
            tokens = self.preprocess_text(doc)
            for token in tokens:
                if doc_id not in self.inverted_index[token]:  # Проверяем, чтобы избежать дубликатов
                    self.inverted_index[token].append(doc_id)
        logger.info("Complete tokenization documents list...")
        # Сортировка doc_id для каждого токена
        for token in self.inverted_index:
            self.inverted_index[token].sort()
            # заполняем остальные списки
            self.fill_list(token)
        logger.info("Complete sorting and encoding list...")

    def fill_list(self, token: str):
        """ Заполнение posting_list_encoded, skip_list_encoded
        inverted_index_skip_list для token """
        # шаг skip list
        step_skip_list = self.get_step_skip_list(len(self.inverted_index[token]))
        # заполняем skip list
        len_item_list = len(self.inverted_index[token])
        for i in range(len_item_list):
            if i % step_skip_list == 0:
                # если попадаем на последний элемент в инв индексе,
                # то не добавляем этот эл-т в skip list
                if i + step_skip_list < len_item_list:
                    num = self.inverted_index[token][i + step_skip_list]
                    self.inverted_index_skip_list[token].append(num)
        # кодируем список
        bin_obj = self.pfordelta_encode(self.inverted_index[token]).bytes
        # сохраняем кодированныы список
        self.posting_list_encoded[token] = bin_obj
        # кодируем skip list и сохраняем
        if len(self.inverted_index_skip_list[token]) > 0:
            bin_obj = self.pfordelta_encode(self.inverted_index_skip_list[token]).bytes
            self.skip_list_encoded[token] = bin_obj

        return

    def set_use_skip_list(self, value: bool):
        """ Сеттер для use_skip_list """
        self.use_skip_list = value
        return

    def get_step_skip_list(self, length: int) -> int:
        """ вычисляем шаг skip list"""
        # шаг skip list
        # согласно книге - Введение в инф. поиск (стр 58)
        # если длина инв. индекса равна P, то следует использовать
        # sqrt(P) равномерно размещенных указателей пропусков
        return round(math.sqrt(length))

    def hasSkip(self, token: str, index: int) -> bool:
        """ Функция показывает, можем ли использовать skip list"""
        # можно использовать skip list? если нет, то False
        if self.use_skip_list == False:
            return False
        #logger.debug("hasSkip. use_skip_list = [%s] ", self.use_skip_list)
        #logger.debug("hasSkip. token = [%s] ", token)
        # Token пуст? то False
        if len(token) == 0:
            return False
        #logger.debug("hasSkip. len(self.inverted_index_skip_list[token]) = [%s] ", len(self.inverted_index_skip_list[token]))
        # Список пуст? то False
        if len(self.inverted_index_skip_list[token]) == 0:
            return False
        # Возвращаем True, если index в posting_list соответствует значению в skip list
        # шаг skip list
        step_skip_list = self.get_step_skip_list(len(self.inverted_index[token]))
        #logger.debug("hasSkip. step_skip_list = [%s], index = %s ", step_skip_list, index)
        # если попадаем на последний элемент в инв индексе,
        # то возвращаем false
        if index + step_skip_list >= len(self.inverted_index[token]):
            result = False
        else:
            result = index % step_skip_list == 0
        #logger.debug("hasSkip. result = [%s] ", result)
        return  result

    def getSkip(self, token: str, index: int) -> int:
        """ Функция возвращает значение на которое указывает skip list """
        # Перед вызовом этой функции должна вызываться hasSkip которая возвращает True
        result = -1
        logger.debug("getSkip. token = [%s] ", token)
        # шаг skip list
        step_skip_list = self.get_step_skip_list(len(self.inverted_index[token]))
        logger.debug("getSkip. step_skip_list = [%s] ", step_skip_list)
        if index + step_skip_list < len(self.inverted_index[token]):
            # // целочисленное деление
            index_skip_list = index // step_skip_list
            result = self.inverted_index_skip_list[token][index_skip_list]
        logger.debug("getSkip. result = [%s] ", result)
        return result

    def hasSkip_encode(self, token: str, index: int) -> bool:
        """ Функция показывает, можем ли использовать skip list
        работает с кодированным списком """
        # мржно использовать skip list? если нет, то False
        if self.use_skip_list == False:
            return False
        # Token пуст? то False
        if len(token) == 0:
            return False
        # Список пуст? то False
        if self.pl_len(self.skip_list_encoded[token]) == 0:
            return False
        # Возвращаем True, если index в posting_list соответствует значению в skip list
        # шаг skip list
        step_skip_list = self.get_step_skip_list(self.pl_len(self.posting_list_encoded[token]))
        # если попадаем на последний элемент в инв индексе,
        # то возвращаем false
        if index + step_skip_list >= self.pl_len(self.posting_list_encoded[token]):
            result = False
        else:
            result = index % step_skip_list == 0
        return  result

    def getSkip_encode(self, token: str, index: int) -> int:
        """ Функция возвращает значение на которое указывает skip list
        работает с кодированным списком """
        # Перед вызовом этой функции должна вызываться hasSkip которая возвращает True
        result = -1
        logger.debug("getSkip_encode. token = [%s] ", token)
        # шаг skip list
        step_skip_list = self.get_step_skip_list(self.pl_len(self.posting_list_encoded[token]))
        logger.debug("getSkip_encode. step_skip_list = [%s] ", step_skip_list)
        if index + step_skip_list < self.pl_len(self.posting_list_encoded[token]):
            index_skip_list = index // step_skip_list
            logger.debug("getSkip_encode. index_skip_list = [%s], index = %s", index_skip_list, index)
            #result = self.skip_list_encoded[token][index_skip_list]
            result = self.pl_get(self.skip_list_encoded[token], index_skip_list)
            logger.debug("getSkip_encode. result = [%s] ", result)
        return result

    def pl_get(self, encode_val, index):
        """функция возвращает раскодированное значение (index)
        из постинг листа (encode_val)"""
        #print(f'encode_val = {encode_val}')
        posting_list = pfordelta_decode(BitStream(bytes=encode_val))
        #print(f'posting_list = {posting_list}')
        return posting_list[index]

    def pl_len(self, encode_val):
        """Функция возвращает общее количество элементов
        в закодированном списке encode_val"""
        if encode_val is not None:
            bits_stream = BitStream(encode_val)
            # Общее кол-во элементов в списке
            count, compress_cnt, bits_count = bits_stream.readlist('int:32, int:32, uint:8')
        else:
            count = 0
        return count

    def preprocess_text(self, text):
        """ разбираем список """
        # Tokenization
        tokens = word_tokenize(text.lower())

        # Stop-word removal
        stop_words = set(stopwords.words('english'))
        tokens = [token for token in tokens if token not in stop_words]

        # Removing punctuation
        tokens = [token for token in tokens if token not in string.punctuation]

        return tokens

    def pfordelta_encode(self, posting_list):
        """ кодирование list по алгоритму pfordelta """
        # Общее кол-во элементов в списке - int
        # Кол-во сжатых элементов - int
        # Кол-во бит используемых для каждого сжатого элемента (используем байт max - 255)
        # Первый элемент (как есть) - int
        # Сжатые эл-ты (массив бит) - bytearray
        # Исключенные элементы в конце списка (как есть) - int

        # вычисляем индекс списка 80% значений
        index_exeption = round(len(posting_list) * 0.8)
        #print(f'index_exeption = {index_exeption}')
        # подсчитываем кол-во бит которым можно закодировать числа
        inc_step = 0
        bits_count = 0
        compress_cnt = 1
        for i in range(len(posting_list)):
            if i != 0:
                inc_step = posting_list[i] - posting_list[i - 1]
                #print(f'inc_step = {inc_step}')
                s = bin(inc_step) #[2:]
                #print(f's = {s}')
                bit_arr = BitArray(bin=s)
                #print(f'i = {i}')
                #print(f'posting_list[i] = {posting_list[i]}')
                #print(f'bit_arr.len = {bit_arr.len}')
                if (bit_arr.len > bits_count) and (i >= index_exeption):
                    # если достигли 80% значений и надо увеличить кол-во байт для хранения
                    # то выходим из цикла, остальные значения будем добавлять как есть
                    break
                compress_cnt = i + 1
                if bit_arr.len > bits_count:
                    bits_count = bit_arr.len
                    #print(f'bits_count = {bits_count}')

        bit_arr = BitArray()
        if bits_count > 0:
            for i in range(compress_cnt): #len(posting_list)):
                # первый эл-т пропускаем (записываем его как есть
                if i == 0:
                    continue
                # получаем дельту между соседними элементами
                # убираем 2 первых символа - 0b
                # дополняем нулями до размерности bits_count
                s = bin(posting_list[i] - posting_list[i - 1])[2:].zfill(bits_count)
                #print(f'bin(posting_list[i]) = {bin(posting_list[i])}')
                #print(f's = {s}')
                bit_arr.append('0b' + s)
            #print(f'bit_arr.bin = {bit_arr.bin}')
            # получаем остаток от деления
            remainder = bit_arr.len % 8
            #print(f'remainder = {remainder}')
            # если остаток не 0, то добиваем до целого байта
            if remainder != 0:
                bit_arr.append('0b' + ''.zfill(8 - remainder))
            #print(f'bit_arr.len = {bit_arr.len}')
            #bit_arr.pp(width=80)
        # Общее кол-во элементов в списке
        res_arr = bitstring.pack('int:32', len(posting_list))
        # Кол-во сжатых элементов
        res_arr += bitstring.pack('int:32', compress_cnt)
        # Кол-во бит используемых для каждого сжатого элемента
        res_arr += bitstring.pack('uint:8', bits_count)

        #res_arr.pp('bin8, hex', width=80)
        # Первый элемент (как есть)
        res_arr += bitstring.pack('int:32', posting_list[0])

        # Сжатые эл-ты
        if bits_count > 0:
            res_arr += bit_arr
        #res_arr.pp('bin8, hex', width=80)

        # проверяем, все ли элементы списка обработали
        # если нет, то дабавляем их в конец без сжатия
        if compress_cnt < len(posting_list):
            #print(f'compress_cnt = {compress_cnt}')
            for i in range(compress_cnt, len(posting_list)):
                #print(f'i = {i}')
                res_arr += bitstring.pack('int:32', posting_list[i])
        #res_arr.pp('bin8, hex', width=80)

        return res_arr


    def dump(self, filepath: str) -> None:
        """Save inverted index to file"""
        with open(filepath, 'wb') as file_io:
            # write count items in index
            count = len(self.inverted_index)
            logger.info("Start saving %s tokens of inverted index to file %s", count, filepath)
            # get packing data
            bin_obj = struct.pack('>i', count)
            # store packing data
            file_io.write(bin_obj)
            i = 0
            for word, article_list in self.inverted_index.items():
                # store word length
                byte_str = word.encode()
                length = len(byte_str)
                bin_obj = struct.pack('>H', length)
                file_io.write(bin_obj)
                # store word
                bin_obj = struct.pack('>' + str(length) + 's', byte_str)
                file_io.write(bin_obj)
                # записываем список
                bin_obj = self.pfordelta_encode(article_list).bytes
                file_io.write(bin_obj)
            logger.info("Complete saving %s tokens of inverted index to file %s", count, filepath)
        return

    @classmethod
    def load(cls, filepath: str) -> InvertedIndex:
        """Loads inverted index from file"""
        with open(filepath, 'rb') as file_io:

            #cls.num_docs = 0
            # read count items in inverted index
            bin_obj = file_io.read(4)
            count = struct.unpack('>i', bin_obj)[0]
            inverted_index_load = defaultdict(list)
            inv_index = InvertedIndex(dict())
            # очищаем кол-во документов перед загрузкой
            inv_index.num_docs = 0
            logger.info("Start loading %s tokens of inverted index to file %s", count, filepath)
            #print(f'count={count}')
            bits_stream = BitStream(file_io)
            for i in range(count):
                bin_obj = file_io.read(2)
                length = struct.unpack('>H', bin_obj)[0]
                #print(f'length={length}')
                # format string for read
                fmt = '>' + str(length) + 's'
                bin_obj = file_io.read(length)
                # unpack string in bytes
                byte_str = struct.unpack(fmt, bin_obj)[0]
                # convert bytes in str
                word = byte_str.decode()
                #print(f'word = {word}')

                # в BitStream устанавливаем указатель
                bits_stream.bytepos = file_io.tell()
                #print(f'bits_stream.read(32).hex = {bits_stream.read(32).hex}')
                #print(f'file_io.tell() = {file_io.tell()}')

                posting_list = pfordelta_decode(bits_stream)
                #print(f'posting_list = [{posting_list}]')
                # добавляем восстановленные числа в список
                inverted_index_load[word] = posting_list
                # подсчитываем общее количество документов
                # так как список отсортирован, то сравниваем с последним элементом
                # 1 добавляем, так как документны нумеруются с 0
                if inv_index.num_docs < posting_list[-1] + 1:
                    inv_index.num_docs = posting_list[-1] + 1
                #bits_stream.bytepos = file_io.tell()
                # перемещаем указатель в файле
                file_io.seek(bits_stream.bytepos)
                #print(f'file_io.tell() = {file_io.tell()}')
        # заполняем созданный класс InvertedIndex считанными значениями
        for key, value in inverted_index_load.items():
            inv_index.inverted_index[key] = value
            # заполняем остальные списки
            inv_index.fill_list(key)
        logger.info("Complete loading %s tokens of inverted index to file %s", count, filepath)
        return inv_index

    def AND(self, posting1, posting2):
        """ AND оператор для list """
        # [0] список, [1] - token
        key1 = posting1[1]
        key2 = posting2[1]
        posting1 = posting1[0]
        posting2 = posting2[0]
        p1 = 0
        p2 = 0
        result = list()
        if (posting1 is not None) and (posting2 is not None):
            while p1 < len(posting1) and p2 < len(posting2):
                if posting1[p1] == posting2[p2]:
                    result.append(posting1[p1])
                    p1 += 1
                    p2 += 1
                elif posting1[p1] > posting2[p2]:
                    # поиск по skip list
                    if self.hasSkip(key2, p2) and (self.getSkip(key2, p2) < posting1[p1]):
                        while self.hasSkip(key2, p2) and (self.getSkip(key2, p2) < posting1[p1]):
                            p2 += self.get_step_skip_list(len(self.inverted_index[key2]))
                            logger.debug("AND. key2 step skip list = [%s] ", self.get_step_skip_list(len(self.inverted_index[key2])))
                    else:
                        p2 += 1
                else:
                    # поиск по skip list
                    if self.hasSkip(key1, p1) and (self.getSkip(key1, p1) < posting2[p2]):
                        while self.hasSkip(key1, p1) and (self.getSkip(key1, p1) < posting2[p2]):
                            p1 += self.get_step_skip_list(len(self.inverted_index[key1]))
                            logger.debug("AND. key1 step skip list = [%s] ", self.get_step_skip_list(len(self.inverted_index[key1])))
                    else:
                        p1 += 1
        return result

    def AND_encode(self, posting1, posting2):
        """ AND оператор для pfordelta """
        # [0] список, [1] - token
        key1 = posting1[1]
        key2 = posting2[1]
        posting1 = posting1[0]
        posting2 = posting2[0]
        p1 = 0
        p2 = 0
        result = list()
        if (posting1 is not None) and (posting2 is not None):
            while p1 < self.pl_len(posting1) and p2 < self.pl_len(posting2):
                # поиск по skip list
                if self.pl_get(posting1, p1) == self.pl_get(posting2,p2):
                    result.append(self.pl_get(posting1, p1))
                    p1 += 1
                    p2 += 1
                elif self.pl_get(posting1, p1) > self.pl_get(posting2, p2):
                    # поиск по skip list
                    if self.hasSkip_encode(key2, p2) and (self.getSkip_encode(key2, p2) < self.pl_get(posting1, p1)):
                        while self.hasSkip_encode(key2, p2) and (self.getSkip_encode(key2, p2) < self.pl_get(posting1, p1)):
                            p2 += self.get_step_skip_list(self.pl_len(self.posting_list_encoded[key2]))
                            logger.debug("AND_encode. key2 step skip list = [%s] ", self.get_step_skip_list(self.pl_len(self.posting_list_encoded[key2])))
                    else:
                        p2 += 1
                else:
                    if self.hasSkip_encode(key1, p1) and (self.getSkip_encode(key1, p1) < self.pl_get(posting2, p2)):
                        while self.hasSkip_encode(key1, p1) and (self.getSkip_encode(key1, p1) < self.pl_get(posting2, p2)):
                            p1 += self.get_step_skip_list(self.pl_len(self.posting_list_encoded[key1]))
                            logger.debug("AND_encode. key1 step skip list = [%s] ", self.get_step_skip_list(self.pl_len(self.posting_list_encoded[key1])))
                    else:
                        p1 += 1
        #print(f'AND_encode result = {result}')
        return result

    def OR(self, posting1, posting2):
        """ OR оператор для list """
        posting1 = posting1[0]
        posting2 = posting2[0]
        p1 = 0
        p2 = 0
        result = list()
        if posting1 is None:
            posting1 = list()
        if posting2 is None:
            posting2 = list()
        while p1 < len(posting1) and p2 < len(posting2):
            if posting1[p1] == posting2[p2]:
                result.append(posting1[p1])
                p1 += 1
                p2 += 1
            elif posting1[p1] > posting2[p2]:
                result.append(posting2[p2])
                p2 += 1
            else:
                result.append(posting1[p1])
                p1 += 1
        while p1 < len(posting1):
            result.append(posting1[p1])
            p1 += 1
        while p2 < len(posting2):
            result.append(posting2[p2])
            p2 += 1
        return result

    def OR_encode(self, posting1, posting2):
        """ OR оператор для pfordelta """
        posting1 = posting1[0]
        posting2 = posting2[0]
        p1 = 0
        p2 = 0
        result = list()
        #if posting2 is None:
        #    posting2 ='0b'
        while p1 < self.pl_len(posting1) and p2 < self.pl_len(posting2):
            if self.pl_get(posting1, p1) == self.pl_get(posting2, p2):
                result.append(self.pl_get(posting1, p1))
                p1 += 1
                p2 += 1
            elif self.pl_get(posting1, p1) > self.pl_get(posting2, p2):
                result.append(self.pl_get(posting2, p2))
                p2 += 1
            else:
                result.append(self.pl_get(posting1, p1))
                p1 += 1
        while p1 < self.pl_len(posting1):
            result.append(self.pl_get(posting1, p1))
            p1 += 1
        while p2 < self.pl_len(posting2):
            result.append(self.pl_get(posting2, p2))
            p2 += 1
        return result

    def NOT(self, posting):
        """ NOT оператор для list """
        posting = posting[0]
        result = list()
        if posting is None:
            posting = list()
        i = 0
        #print(f'posting = {posting}')
        for item in posting:
            while i < item:
                result.append(i)
                i += 1
            else:
                i += 1
        else:
            while i < self.num_docs: #NUM_OF_DOCS:
                result.append(i)
                i += 1
        logger.debug("NOT. self.num_docs = %s", self.num_docs)
        return result

    def NOT_encode(self, posting):
        """ NOT оператор для pfordelta """
        posting = posting[0]
        result = list()
        i = 0
        for item in pfordelta_decode(BitStream(posting)):
            while i < item:
                result.append(i)
                i += 1
            else:
                i += 1
        else:
            while i < self.num_docs: #NUM_OF_DOCS:
                result.append(i)
                i += 1
        logger.debug("NOT_encode. self.num_docs = %s", self.num_docs)
        return result

    def postfix(self, infix_tokens):
        """ разбиваем запрос на составляющие"""
        #precendence initialization
        precedence = {}
        precedence['NOT'] = 3
        precedence['AND'] = 2
        precedence['OR'] = 1
        precedence['('] = 0
        precedence[')'] = 0

        output = []
        operator_stack = []

        #creating postfix expression
        for token in infix_tokens:
            if (token == '('):
                operator_stack.append(token)

            elif (token == ')'):
                operator = operator_stack.pop()
                while operator != '(':
                    output.append(operator)
                    operator = operator_stack.pop()

            elif (token in precedence):
                if (operator_stack):
                    current_operator = operator_stack[-1]
                    while (operator_stack and precedence[current_operator] > precedence[token]):
                        output.append(operator_stack.pop())
                        if (operator_stack):
                            current_operator = operator_stack[-1]

                operator_stack.append(token)

            else:
                output.append(token.lower())

        #while staack is not empty appending
        while (operator_stack):
            output.append(operator_stack.pop())
        return output

    #Boolean query processing
    def process_query(self, q):
        """ запуск запроса """
        q = q.replace('(', '( ')
        q = q.replace(')', ' )')
        q = q.split(' ')
        query = []

        for i in q:
            query.append(i) #(ps.stem(i))
        for i in range(0,len(query)):
            if ( query[i]== 'and' or query[i]== 'or' or query[i]== 'not'):
                query[i] = query[i].upper()
        results_stack = []
        postfix_queue = self.postfix(query)

        #return postfix_queue
        #evaluating postfix query expression
        for i in postfix_queue:
            if ( i!= 'AND' and i!= 'OR' and i!= 'NOT'):
                i = i.replace('(', ' ')
                i = i.replace(')', ' ')
                key = i.lower()
                posting_list = self.inverted_index.get(key) #dictionary_inverted.get(i)
                if posting_list is None:
                    key = ''
                #print(f'posting_list = {posting_list}')
                results_stack.append([posting_list, key])
            elif (i=='AND'):
                a = results_stack.pop()
                b = results_stack.pop()
                results_stack.append([self.AND(a, b), '']) #(AND_op(a,b))
            elif (i=='OR'):
                a = results_stack.pop()
                b = results_stack.pop()
                results_stack.append([self.OR(a, b), '']) #(OR_op(a,b))
            elif (i == 'NOT'):
                a = results_stack.pop()
                results_stack.append([self.NOT(a), '']) #(NOT_op(a,doc_ids))

        res =  results_stack.pop()
        return res[0]

    def process_query_encode(self, q):
        """Boolean query processing with encoded list"""
        q = q.replace('(', '( ')
        q = q.replace(')', ' )')
        q = q.split(' ')
        query = []

        for i in q:
            query.append(i) #(ps.stem(i))
        for i in range(0,len(query)):
            if ( query[i]== 'and' or query[i]== 'or' or query[i]== 'not'):
                query[i] = query[i].upper()
        results_stack = []
        postfix_queue = self.postfix(query)

        #return postfix_queue
        #evaluating postfix query expression
        for i in postfix_queue:
            if ( i!= 'AND' and i!= 'OR' and i!= 'NOT'):
                i = i.replace('(', ' ')
                i = i.replace(')', ' ')
                key = i.lower()
                posting_list = self.posting_list_encoded.get(key)
                if posting_list is None:
                    key = ''
                #print(f'encode i = {i}')
                results_stack.append([posting_list, key])
            elif (i=='AND'):
                a = results_stack.pop()
                b = results_stack.pop()
                results_stack.append([self.AND_encode(a, b), ''])
            elif (i=='OR'):
                a = results_stack.pop()
                b = results_stack.pop()
                results_stack.append([self.OR_encode(a, b), ''])
            elif (i == 'NOT'):
                a = results_stack.pop()
                #print(f'query_encode NOT = {pfordelta_decode(BitStream(a))}')
                results_stack.append([self.NOT_encode(a), ''])

        res =  results_stack.pop()
        res = res[0]
        if isinstance(res, bytes):
            res = pfordelta_decode(BitStream(res))
        return res # results_stack.pop()


    def __repr__(self):
        repr_ = f"{self.inverted_index}"
        return repr_

    def __eq__(self, rhs):
        outcome = (
            self.inverted_index == rhs.inverted_index
        )
        return outcome

In [21]:
def pfordelta_decode( bits_stream: BitStream) -> list:
    """ раскодирование list по алгоритму pfordelta """
    posting_list = []
    # если длина 0, то и читать нечего, возвращаем пустой список
    if bits_stream.length == 0:
        return posting_list
    # Общее кол-во элементов в списке
    # Кол-во сжатых элементов
    # Кол-во бит используемых для каждого сжатого элемента
    count, compress_cnt, bits_count = bits_stream.readlist('int:32, int:32, uint:8')
    # Первый элемент (как есть)
    first_num = bits_stream.read('int:32')
    posting_list.append(first_num)
    # inverted_index_load[word].append(first_num)
    # Сжатые эл-ты
    if bits_count > 0:
        last_num = first_num
        for i in range(compress_cnt): #len(posting_list)):
            # первый эл-т пропускаем (записываем его как есть
            if i == 0:
                continue
            # получаем дельту между соседними элементами
            # нужное кол-во бит
            delta = bits_stream.read(bits_count)
            #print(f'delta.int = {delta.uint}')
            last_num += delta.uint
            # добавляем восстановленное число в список
            posting_list.append(last_num)
            # inverted_index_load[word].append(last_num)
    # выравниваем по байту
    bits_stream.bytealign()
    # проверяем, все ли элементы списка обработали
    # если нет, то дабавляем их в конец без сжатия
    if compress_cnt < count:
        for i in range(compress_cnt, count):
            #print(f'i = {i}')
            num = bits_stream.read('int:32')
            posting_list.append(num)

    return posting_list

In [23]:
def load_documents(filepath: str) -> list[str]:
    """Loads documents from file"""
    logger.info("reading documents file...")
    documents = []
    with open(filepath, encoding='utf-8') as file_io:
        i = 0
        for line in file_io.readlines():
            #if i > 1000:
            #    break
            documents.append(line)
            i += 1
    logger.info("reading complete. Read %s documents.", len(documents))
    return documents

In [25]:
# Создание инвертированного индекса
def build_inverted_index(documents) -> InvertedIndex:
    """ Build inverted index """
    inv_index = InvertedIndex(documents)
    return inv_index

In [28]:
def main():
    """Main function"""
    # задаем формат вывода сообщений лога
    logging.basicConfig(
        format='%(asctime)s.%(msecs)03d %(levelname)-8s %(message)s',
        level=logging.INFO,
        datefmt='%Y-%m-%d %H:%M:%S')

    logger.setLevel(logging.INFO)

    # читаем документы из файла
    big_docs = load_documents(DATASET_BIG_PATH)
    # строим инвертированный индекс
    inverted_index = build_inverted_index(big_docs)

    queries = ['Анна', 'Упал OR шел', 'Понимает AND забываешь',
                'Увлечение AND повторится',
                'Судить OR могу',
                'NOT провела'
                ]
    inverted_index.set_use_skip_list(True)
    for query in queries:
        logger.info("Start searching [%s] in simple list", query)
        res_list_simple = inverted_index.process_query(query)
        res_list_encode = inverted_index.process_query_encode(query)
        logger.info("Complete search [%s] in encode list", query)

    print(inverted_index.inverted_index)

In [30]:
main()

2024-06-11 12:44:15.046 INFO     reading documents file...
2024-06-11 12:44:15.063 INFO     reading complete. Read 21244 documents.
2024-06-11 12:44:15.064 INFO     Start tokenization documents list...
2024-06-11 12:44:20.614 INFO     Complete tokenization documents list...
2024-06-11 12:44:25.268 INFO     Complete sorting and encoding list...
2024-06-11 12:44:25.268 INFO     Start searching [Анна] in simple list
2024-06-11 12:44:25.272 INFO     Complete search [Анна] in encode list
2024-06-11 12:44:25.273 INFO     Start searching [Упал OR шел] in simple list
2024-06-11 12:44:25.347 INFO     Complete search [Упал OR шел] in encode list
2024-06-11 12:44:25.348 INFO     Start searching [Понимает AND забываешь] in simple list
2024-06-11 12:44:25.361 INFO     Complete search [Понимает AND забываешь] in encode list
2024-06-11 12:44:25.362 INFO     Start searching [Увлечение AND повторится] in simple list
2024-06-11 12:44:25.363 INFO     Complete search [Увлечение AND повторится] in encode l

defaultdict(<class 'list'>, {'лев': [0, 17415, 17417, 17419, 17421, 17423], 'толстой': [0, 10709, 17413, 17415, 17417, 17419, 17421, 17423, 17425, 17427, 17429, 17431, 17433, 17435, 17437, 17439, 17441, 17470, 17547, 17712, 17734, 17789, 17877, 17888, 17987, 18081, 18235, 18785, 18972, 19115, 19236, 19302, 20380, 20512, 20666, 20743, 20908, 20919, 20996, 21029, 21040, 21051, 21073, 21095, 21172, 21205, 21227], 'анна': [2, 80, 82, 224, 1526, 1560, 1570, 1589, 1593, 1607, 1613, 1619, 1623, 1631, 1645, 1649, 1653, 1663, 1669, 1671, 1673, 1679, 1693, 1706, 1710, 1712, 1720, 1728, 1732, 1736, 1738, 1742, 1756, 1762, 1766, 1774, 1778, 1782, 1797, 1805, 1809, 1813, 1817, 1823, 1835, 1837, 1841, 1882, 1884, 1890, 1894, 1904, 1917, 1947, 1955, 1959, 1961, 1965, 1967, 1971, 1973, 2266, 2272, 2276, 2280, 2284, 2290, 2294, 2296, 2298, 2302, 2304, 2316, 2318, 2320, 2326, 2334, 2336, 2351, 2353, 2386, 2423, 2439, 2460, 2468, 2472, 2478, 2486, 2488, 2503, 2507, 2519, 2523, 2539, 2545, 2547, 2551, 286

In [31]:
import time

In [32]:
exec_time_encode = []
exec_time_build = []

#задаем формат вывода сообщений лога
logging.basicConfig(
    format='%(asctime)s.%(msecs)03d %(levelname)-8s %(message)s',
    level=logging.INFO,
    datefmt='%Y-%m-%d %H:%M:%S')

logger.setLevel(logging.INFO)

# читаем документы из файла
big_docs = load_documents(DATASET_BIG_PATH)
# строим инвертированный индекс
for i in range(10):
    start = time.perf_counter()
    inverted_index = build_inverted_index(big_docs)
    end = time.perf_counter() - start
    exec_time_build.append(end * 1000)

queries = ['Анна', 'Упал OR шел', 'Понимает AND забываешь',
                'Увлечение AND повторится',
                'Судить OR могу',
                'NOT провела'
                ]

inverted_index.set_use_skip_list(True)

for i in range(10):
    for query in queries:
        logger.info("Start searching [%s] in encode list", query)
        start = time.perf_counter()
        res_list_encode = inverted_index.process_query_encode(query)
        end = time.perf_counter() - start
        exec_time_encode.append(end * 1000)
        logger.info("Complete search [%s] in encode list", query)

2024-06-11 12:44:26.162 INFO     reading documents file...
2024-06-11 12:44:26.178 INFO     reading complete. Read 21244 documents.
2024-06-11 12:44:26.179 INFO     Start tokenization documents list...
2024-06-11 12:44:31.739 INFO     Complete tokenization documents list...
2024-06-11 12:44:36.460 INFO     Complete sorting and encoding list...
2024-06-11 12:44:36.461 INFO     Start tokenization documents list...
2024-06-11 12:44:42.263 INFO     Complete tokenization documents list...
2024-06-11 12:44:47.147 INFO     Complete sorting and encoding list...
2024-06-11 12:44:47.151 INFO     Start tokenization documents list...
2024-06-11 12:44:52.764 INFO     Complete tokenization documents list...
2024-06-11 12:44:57.293 INFO     Complete sorting and encoding list...
2024-06-11 12:44:57.299 INFO     Start tokenization documents list...
2024-06-11 12:45:02.661 INFO     Complete tokenization documents list...
2024-06-11 12:45:07.167 INFO     Complete sorting and encoding list...
2024-06-11 1

In [33]:
import numpy as np

In [34]:
print(f"Время построения индекса: {np.mean(exec_time_build)} ms")
print(f"Время поиска {np.mean(exec_time_encode)} ms")

Время построения индекса: 10102.460379945114 ms
Время поиска 120.06552827854951 ms


In [35]:
# записываем инвертированный индекс на диск
time_write = []
for i in range(10):
    start = time.perf_counter()
    inverted_index.dump(DEFAULT_INVERTED_INDEX_STORE_PATH)
    end = time.perf_counter() - start
    time_write.append(end * 1000)
print(f"Время сохранения на диск {np.mean(time_write)} ms")

2024-06-11 12:46:14.528 INFO     Start saving 36223 tokens of inverted index to file D:\Documents\ИТМО\Учёба\2 семестр\Структуры и алгоритмы индексации данных\инвертированный индекс лаб 4\anna_inverted_index.bin
2024-06-11 12:46:18.100 INFO     Complete saving 36223 tokens of inverted index to file D:\Documents\ИТМО\Учёба\2 семестр\Структуры и алгоритмы индексации данных\инвертированный индекс лаб 4\anna_inverted_index.bin
2024-06-11 12:46:18.102 INFO     Start saving 36223 tokens of inverted index to file D:\Documents\ИТМО\Учёба\2 семестр\Структуры и алгоритмы индексации данных\инвертированный индекс лаб 4\anna_inverted_index.bin
2024-06-11 12:46:21.607 INFO     Complete saving 36223 tokens of inverted index to file D:\Documents\ИТМО\Учёба\2 семестр\Структуры и алгоритмы индексации данных\инвертированный индекс лаб 4\anna_inverted_index.bin
2024-06-11 12:46:21.607 INFO     Start saving 36223 tokens of inverted index to file D:\Documents\ИТМО\Учёба\2 семестр\Структуры и алгоритмы индек

Время сохранения на диск 3516.4084000512958 ms


In [36]:
# считываем инвертированный индекс из файла
time_load = []
for i in range(10):
    start = time.perf_counter()
    inverted_index_load = InvertedIndex.load(DEFAULT_INVERTED_INDEX_STORE_PATH)
    end = time.perf_counter() - start
    time_load.append(end * 1000)
print(f"Время cчитывания с диска {np.mean(time_load)} ms")
print(f'inverted_index_load = {inverted_index_load.inverted_index}')

2024-06-11 12:46:49.707 INFO     Start tokenization documents list...
2024-06-11 12:46:49.707 INFO     Complete tokenization documents list...
2024-06-11 12:46:49.708 INFO     Complete sorting and encoding list...
2024-06-11 12:46:49.709 INFO     Start loading 36223 tokens of inverted index to file D:\Documents\ИТМО\Учёба\2 семестр\Структуры и алгоритмы индексации данных\инвертированный индекс лаб 4\anna_inverted_index.bin
2024-06-11 12:46:56.684 INFO     Complete loading 36223 tokens of inverted index to file D:\Documents\ИТМО\Учёба\2 семестр\Структуры и алгоритмы индексации данных\инвертированный индекс лаб 4\anna_inverted_index.bin
2024-06-11 12:46:56.686 INFO     Start tokenization documents list...
2024-06-11 12:46:56.687 INFO     Complete tokenization documents list...
2024-06-11 12:46:56.687 INFO     Complete sorting and encoding list...
2024-06-11 12:46:56.688 INFO     Start loading 36223 tokens of inverted index to file D:\Documents\ИТМО\Учёба\2 семестр\Структуры и алгоритмы и

Время cчитывания с диска 7019.234259892255 ms
inverted_index_load = defaultdict(<class 'list'>, {'лев': [0, 17415, 17417, 17419, 17421, 17423], 'толстой': [0, 10709, 17413, 17415, 17417, 17419, 17421, 17423, 17425, 17427, 17429, 17431, 17433, 17435, 17437, 17439, 17441, 17470, 17547, 17712, 17734, 17789, 17877, 17888, 17987, 18081, 18235, 18785, 18972, 19115, 19236, 19302, 20380, 20512, 20666, 20743, 20908, 20919, 20996, 21029, 21040, 21051, 21073, 21095, 21172, 21205, 21227], 'анна': [2, 80, 82, 224, 1526, 1560, 1570, 1589, 1593, 1607, 1613, 1619, 1623, 1631, 1645, 1649, 1653, 1663, 1669, 1671, 1673, 1679, 1693, 1706, 1710, 1712, 1720, 1728, 1732, 1736, 1738, 1742, 1756, 1762, 1766, 1774, 1778, 1782, 1797, 1805, 1809, 1813, 1817, 1823, 1835, 1837, 1841, 1882, 1884, 1890, 1894, 1904, 1917, 1947, 1955, 1959, 1961, 1965, 1967, 1971, 1973, 2266, 2272, 2276, 2280, 2284, 2290, 2294, 2296, 2298, 2302, 2304, 2316, 2318, 2320, 2326, 2334, 2336, 2351, 2353, 2386, 2423, 2439, 2460, 2468, 2472, 2